In [83]:
# pip install spacy
# python -m spacy download it_core_news_sm

import os
import re
import pandas as pd
from nltk.corpus import stopwords
import spacy
import math
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

### Utils

In [84]:
stop_words = set(stopwords.words('italian')) #remove stop words
lemmatizer = spacy.load('it_core_news_sm')

def pre_processing(document):
    document = re.sub(r'[^\w\s]',' ',document) #remove punctuation
    document = document.lower()
    document = lemmatizer(document)
    document = [token.lemma_ for token in document]
    document = [w for w in document if not w in stop_words]
    return document

#inverse document frequency
def idf(word, documents_list):
    return math.log10(len(documents_list)/sum([1.0 for i in documents_list if word in i.testo]))

#term frequency
def tf(word, document_words):
    return document_words.count(word)/len(document_words)

In [85]:
class Documento:
    # ============================================
    # Constructor
    # ============================================
    def __init__(self, titolo, classe, testo):
        self.titolo = titolo
        self.classe = classe
        self.testo = testo
        self.term_vector = []

    def __str__(self):
        return "Titolo: " + self.titolo + "\nClasse: " + self.classe

In [86]:
class ListaDocumenti:
    # ============================================
    # Constructor
    # ============================================
    def __init__(self):
        self.documenti = []
        self.classi = set()
        self.vocabolario = set()

    def __str__(self):
        return "#documenti: " + str(len(self.documenti)) + ", #classi: " + str(len(self.classi)) + ", #vocabolario: " + str(len(self.vocabolario))
    
    # ============================================
    # Public Methods
    # ============================================
    def add_documento(self, documento):
        self.documenti.append(documento)
        self.classi.add(documento.classe)
        self.vocabolario.update(documento.testo)

    def calculate_term_vectors(self):
        for documento in self.documenti:
            weights = {}
            for word in self.vocabolario:
                weights.update({word: tf(word, documento.testo) * idf(word, self.documenti)})
            documento.term_vector = weights
            print('term vector', documento.term_vector)
        

### Vector space model

In [87]:
'''
Calcola il vector space model
'''
def generate_vsm():
    path = "data\docs_200"

    lista_documenti = ListaDocumenti()

    for file_name in os.listdir(path):
        if os.path.isfile(os.path.join(path, file_name)):
            file = open("data/docs_200/" + file_name, "r", encoding="utf-8")
            classe = file_name.split("_")[0]
            sentence = pre_processing(file.read().replace("\n", " ").replace("\"", ""))
            sentence = sentence[:30]

            lista_documenti.add_documento(Documento(file_name, classe, sentence))

    return lista_documenti

### Metodo di Rocchio

#### Calcolo dei prototipi (training)

In [88]:
class Prototipo:
    # ============================================
    # Constructor
    # ============================================
    def __init__(self, classe, profile_vector):
        self.classe = classe
        self.profile_vector = profile_vector

    def __str__(self):
        return "Classe: " + self.classe + "\nProfile vector: " + str(self.profile_vector)

In [89]:
class Rocchio:
    # ============================================
    # Constructor
    # ============================================
    def __init__(self, vocabolario, classi):
        self.prototipi = []
        self.vocabolario = vocabolario
        self.classi = classi
        
    def __str__(self):
        return "Classe: " + self.classe + "\nProfile vector: " + str(self.profile_vector)
    
    # ============================================
    # Private Methods
    # ============================================

    def _add_prototipo(self, prototipo):
        self.prototipi.append(prototipo) 

    # restituisce il documento più simile al documento positivo
    def _get_nearest_doc(self, positive_doc, documenti_training):
        max_similarity = 0
        nearest_doc = None
        for doc in documenti_training:
            if doc.classe != positive_doc.classe:
                positive_doc_s = np.array(list(positive_doc.term_vector.values())).reshape(1, -1)
                doc_s = np.array(list(doc.term_vector.values())).reshape(1, -1)
                similarity = cosine_similarity(positive_doc_s, doc_s)[0][0]
                if similarity > max_similarity:
                    max_similarity = similarity
                    nearest_doc = doc
        return nearest_doc
    
    #metodo per calcolare i documenti near positive
    def near_positive_documents(self, classe_pos, documenti_training):
        near_positive_documents = []
        for doc in documenti_training:
            if doc.classe == classe_pos:
                near_positive_documents.append(self._get_nearest_doc(doc, documenti_training))

        return near_positive_documents

    def _calcola_prototipo_rocchio(self, classe, documenti_training, beta, gamma):
        contributi_pos = {}
        contributi_near_pos = {}
        for word in self.vocabolario:
            contributi_pos.update({word: 0})
            contributi_near_pos.update({word: 0})

        near_pos = self.near_positive_documents(classe, documenti_training)

        # contributo dei positivi
        count_pos = 0
        for doc in documenti_training:
            if doc.classe == classe:
                for word in self.vocabolario:
                    contributi_pos[word] += doc.term_vector[word]
                count_pos += 1
        for word in self.vocabolario:
            contributi_pos[word] /= count_pos

        # contributo dei near positive
        count_near_pos = 0
        for n_pos in near_pos:
            for word in self.vocabolario:
                contributi_near_pos[word] -= n_pos.term_vector[word]
            count_near_pos += 1

        for word in self.vocabolario:
            contributi_near_pos[word] /= count_near_pos

        # calcolo del prototipo
        prototipo = {}
        for word in self.vocabolario:
            prototipo[word] = beta * contributi_pos[word] - gamma * contributi_near_pos[word]
    
        return Prototipo(classe, prototipo)
    
    # ============================================
    # Public Methods
    # ============================================    
    def train(self, documenti_training, beta=4, gamma=16):
        for classe in self.classi:
            self._add_prototipo(self._calcola_prototipo_rocchio(classe, documenti_training, beta, gamma))
    
    def score(self, test_set):
        score = 0
        for doc in test_set:
            max_similarity = 0
            for prototipo in self.prototipi:
                doc_s = np.array(list(doc.term_vector.values())).reshape(1, -1)
                prototipo_s = np.array(list(prototipo.profile_vector.values())).reshape(1, -1)
                similarity = cosine_similarity(doc_s, prototipo_s)[0][0]
                if similarity > max_similarity:
                    max_similarity = similarity
                    classe = prototipo.classe
            if classe == doc.classe:
                score += 1
        return score/len(test_set)*100

##### cross-validation

In [90]:
def cross_val_score(lista_documenti, cv=5, gamma=16, beta=4):
    scores = []
 
    modello_rocchio = Rocchio(lista_documenti.vocabolario, lista_documenti.classi)

    #shuffle documents
    documents_permutato = np.random.permutation(lista_documenti.documenti)

    #divide x in cv parti
    data_folds = np.array_split(documents_permutato, cv)

    for i in range(cv):
        current_data_training_set = np.concatenate(data_folds[:i] + data_folds[i+1:], axis=0)
        current_data_test_set = data_folds[i]

        modello_rocchio.train(current_data_training_set, gamma, beta)
        score = modello_rocchio.score(current_data_test_set)
        print("Fold " + str(i) + ": " + str(score) + " %")

        scores.append(score)
    
    return scores

- Beta: Il parametro beta controlla l'effetto del termine medio della classe negativa sul calcolo del vettore rappresentativo della classe di riferimento. Un valore più grande di beta enfatizza maggiormente il termine medio della classe negativa, mentre un valore più piccolo lo enfatizza meno. La scelta di beta dipende dalla distribuzione dei dati e dalle preferenze specifiche dell'utente. In generale, valori compresi tra 0 e 1 sono comuni per beta.
- Gamma: Il parametro gamma influenza il calcolo del vettore rappresentativo della classe negativa. Un valore più grande di gamma riduce l'effetto dei documenti della classe negativa, mentre un valore più piccolo lo aumenta. La scelta di gamma dipende dalla distribuzione dei dati e dalle preferenze specifiche dell'utente. Valori compresi tra 0 e 1 sono comuni per gamma.

In [91]:
lista_documenti = generate_vsm()

In [92]:
lista_documenti.calculate_term_vectors()

term vector {'neonato': 0.0, 'giocatore': 0.0, 'bloomberg': 0.0, 'eventuale': 0.0, 'acquisizione': 0.0, 'periodo': 0.0, 'distanza': 0.0, 'election': 0.0, 'intero': 0.0, 'emorragia': 0.0, 'influenza': 0.0, 'pregare': 0.0, 'opposto': 0.0, 'dossier': 0.0, 'company': 0.0, 'cielo': 0.0, 'ora': 0.0, 'ecco': 0.0, 'minacciare': 0.0, 'giungere': 0.0, 'scontro': 0.0, 'nanometrico': 0.0, 'ripartire': 0.0, 'profumo': 0.0, 'Unesco': 0.0, 'organizzare': 0.0, 'civile': 0.0, 'quarant': 0.0, 'centro': 0.0, 'espulsione': 0.0, 'brare': 0.0, 'australiano': 0.0, 'cosidderre': 0.0, 'incostituzionale': 0.0, 'nadal': 0.0, '19': 0.0, 'Natale': 0.0, 'area': 0.0, 'champagna': 0.0, 'ruolo': 0.0, 'sema': 0.0, 'ibrida': 0.0, 'dovere': 0.0, 'bianco': 0.0, 'rispetto': 0.0, 'assumere': 0.0, 'recessione': 0.0, 'qui': 0.0, 'trentino': 0.0, '76': 0.0, 'vedere': 0.0, 'aggiungere': 0.0, 'automobilismo': 0.0, 'alvaro': 0.0, 'presentazione': 0.0, 'relativo': 0.0, 'epilessia': 0.0, 'sostuire': 0.0, 'successione': 0.0, 'esclud

In [95]:
accuracies = cross_val_score(lista_documenti, cv=5, gamma=16, beta=4)

Fold 0: 45.0 %
Fold 1: 100.0 %
Fold 2: 97.5 %
Fold 3: 100.0 %
Fold 4: 97.5 %


In [93]:
best_gamma = 0
best_beta = 0
best_accuracy = 0
for i in range(20):
    for j in range(20):
        print("Iterazione", str(i+1), str(j+1))
        accuracies = cross_val_score(lista_documenti, cv=2, gamma=i+1, beta=j+1)
        print('\n')
        for accuracy in accuracies:
            if accuracy > best_accuracy:
                best_accuracy = accuracy
                best_gamma = i+1
                best_beta = j+1

Iterazione 1 1


Fold 0: 42.0 %
Fold 1: 70.0 %


Iterazione 1 2
Fold 0: 30.0 %
Fold 1: 48.0 %


Iterazione 1 3
Fold 0: 16.0 %
Fold 1: 48.0 %


Iterazione 1 4
Fold 0: 22.0 %
Fold 1: 41.0 %


Iterazione 1 5
Fold 0: 19.0 %
Fold 1: 44.0 %


Iterazione 1 6
Fold 0: 16.0 %
Fold 1: 37.0 %


Iterazione 1 7
Fold 0: 13.0 %


KeyboardInterrupt: 